## Proyecto B: Calculadora de ReTweets

Inicialmente, debemos construir un dataset con la mayor cantidad de tweets en Colombia durante la última semana. Para ello, seleccionamos un total de 100604 tweets de la API de Twitter publicados del 15 al 21 de Febrero.

In [1]:
# Libraries
from gensim.models.word2vec import Word2Vec
import pandas as pd
import numpy as np
import gradio as gr
import re
import nltk
from unidecode import unidecode
from nltk import stem
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import HashingVectorizer
from scipy.sparse.linalg import svds as SparseSVD
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error

In [2]:
file = open('data/spanish_stop_words.txt',encoding='UTF-8')
SPANISH_STOP_WORDS = file.read().split()
file.close()

### Análisis de Tópicos

In [3]:
def preprocessing(d):
    # d -> document

    removed = re.sub(r'http\S+', '', d) # removes links from tweet
    words = removed.split()
    # Convert to lowercase every word  
    prep = [w.lower() for w in words]

    # Remove Spanish Stop Words
    prep = [w for w in prep if w not in SPANISH_STOP_WORDS]

    # Perform Unidecode normalization for removing accentuations, special characters etc.
    prep = [unidecode(w) for w in prep]

    # Remove special characters and punctuation
    prep = [re.sub('[^A-Za-z0-9]+', '', w) for w in prep]
    
    # Remove empty strings
    prep = [w for w in prep if w != '']
    
    # Lemmatization
    wnl = stem.WordNetLemmatizer()        
    prep = [wnl.lemmatize(w) for w in prep]
    
    
    processed_string = ' '.join(prep)
    if processed_string == "":
        return 'i' # just a neutral letter, that doesn't give much information as the empty string. This only happens when a tweet is fully contained out of spanish stop words
    return processed_string

# Testing HyperParameter

In [4]:
def vectorized_tweet(model, tweet):
    vectorized_tweet = []
    for word in tweet:
        vectorized_tweet.append(model.wv.get_vector(word))
    return np.average(vectorized_tweet,axis=0)

def BuildAndTrainModel(corpus, y, vector_size=500, min_count = 1, workers = 20, sg=1, window = 30, sample = 1e-6, random_seed = 42):
    '''Receives Corpus and y
    Corpus is a list of documents. In this context a list of tweets
    Y is the regression target for the given document. In this context, the number of retweets.
    INCLUDES PREPROCESSING
    Builds a word2vec model with given parameters, and then creates and trains Random Forest Regressor

    Returns: The trained word2vec model, and the fitted random forest regressor'''
    prep = [preprocessing(d) for d in corpus]
    
    sentences = []
    for document in prep:
        sentences.append(document.split())
    model = Word2Vec(sentences=sentences, vector_size=vector_size, window=window, min_count=min_count, workers=workers, sg=sg, sample=sample,
            seed=random_seed)

    X = np.row_stack([vectorized_tweet(model, x) for x in sentences])
    regr = RandomForestRegressor(max_depth = 3, random_state = random_seed, n_jobs=-1)
    regr.fit(X,y)
    return model, regr

In [5]:
def getNewTweetVector(model, tweet): # Intented for a single tweet 
  tweet = preprocessing(tweet)
  words = tweet.split(' ')
  missing_words = [x for x in words if x not in model.wv.key_to_index]
  if len(missing_words) > 0:
    ## adding a word to the model
    model.build_vocab([missing_words], update=True)
    model.train([missing_words], total_examples=model.corpus_count, epochs=model.epochs)
  return vectorized_tweet(model, words)

def getNewTweetVectorsMultiple(model, tweets): # Intended for a multiple list of tweets, for more efficiency
    list_of_tweets = [preprocessing(tw) for tw in tweets]
    list_of_words = [tw.split(' ') for tw in list_of_tweets]
    new_sentences = [] # only add sentences which aren't already in the model.
    for sentence in list_of_words:
        for word in sentence:
          if word not in model.wv.key_to_index:
            new_sentences.append(sentence)
            break 
    
    if len(new_sentences) > 0:
        print(f"Adding {len(new_sentences)} new sentences to model")
        ## add new sentences to model
        model.build_vocab(new_sentences, update=True)
        model.train(new_sentences, total_examples=model.corpus_count, epochs=model.epochs)
    # get vectorized tweets with our newly updated model
    return np.row_stack([vectorized_tweet(model, x) for x in list_of_words])


In [6]:
def TestModelRMSE(model, regr, test_tweets, y_test):
    X_test = getNewTweetVectorsMultiple(model, test_tweets)
    y_predicted = regr.predict(X_test)
    return mean_squared_error(y_test, y_predicted, squared=False)

In [7]:
feb21 = pd.read_csv(f'data/period6.csv')
X_train, X_test, y_train, y_test = train_test_split(feb21["tweet"], feb21["retweet_count"], test_size=0.2, random_state=42)
model, regr = BuildAndTrainModel(X_train,y_train, vector_size=500, min_count = 1, workers = 1, sg=1, window = 30, sample = 1e-6, random_seed=42)
print("Root Mean Squared Error (RMSE) = ", TestModelRMSE(model, regr, X_test, y_test))

Adding 1479 new sentences to model
Root Mean Squared Error (RMSE) =  35.54985896748519


## Find most important words

In [8]:
words2retweet = pd.DataFrame(columns = ["words", "retweet_value"])
words2retweet["words"] = model.wv.index_to_key
words2retweet["retweet_value"] = regr.predict(model.wv.vectors)

In [9]:
pd.set_option("display.max_rows", None)
words2retweet.sort_values(by=['retweet_value'], ascending=False)

words  retweet_value
14667                                          minecraft    1203.029311
1421                                           entidades    1126.668504
14007                                          enviarian    1088.852079
6915                                            exportar     785.650292
19608                                         perseguida     759.982640
22850                                        slideplayer     755.083079
22242                                              chivo     752.830783
4897                                             agredio     751.279234
3817                                       eduardobittar     749.765697
5115                                             viejita     745.618927
15532                                            ganarla     743.457178
8462                                         davidracero     739.080800
4509                                            dictador     736.929352
9470                                           encargada     733.257453
14677                                              chicx     732.611479
17730                                          compramos     731.292344
11318                                             gamine     729.880945
417                                               perdio     727.960953
22598                                         marginadas     723.460713
8752                                         guadalajara     722.840969
3511                                              tarado     721.425218
15253                                    brandon89934206     720.592391
3406                                              brutal     718.348736
11916                                         clasifique     718.035917
16558                                                hbo     716.549479
20411                                         disidentes     716.379261
8125                                       policiacucuta     714.602745
15634                                           malisimo     714.382015
8037                                noticiascaracolahora     713.716078
25878                                           mandatoy     713.706277
8102                                           cotidiana     711.717446
9267                                             metidos     710.241238
5264                                       abortolibreya     709.408846
2993                                           21febrero     707.647903
11267                                        cuestionado     705.524732
13406                                              danen     703.525854
22906                                              cicla     703.438419
10921                                            lapidas     703.408054
15169                                                ayy     703.097302
7112                                            lanzando     702.806338
2598                                               parte     702.646982
18739                                     karina52201055     700.923992
10802                                             remate     700.073725
9237                                                 eua     699.512059
8719                                              acusar     699.304496
16144                               nosqueremosdecididas     699.120195
9386                                             padecen     697.854692
18763                                          garantida     697.095389
9306                                            sucursal     696.926554
26179                                               vaca     695.707271
2953                                              muchos     695.335923
790                                                 nota     695.041053
4422                                            leopoldo     695.039204
25490                                     jack1100936777     694.922825
12267                                   fundamentalmente     694.504135
18886              